Our first method will use simple counting i.e. count the number of times each character is predicted based on two characters provided e.g. the name jane would defines n as the next characters after 'ja' so that would add to 'n' probability of being the next character 

In [1]:
import math
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline 
%pip install torch torchvision
import torch

Note: you may need to restart the kernel to use updated packages.


In [3]:
# Read in words
words = open('names.txt', 'r').read().splitlines()
words[:10]


['emma',
 'olivia',
 'ava',
 'isabella',
 'sophia',
 'charlotte',
 'mia',
 'amelia',
 'harper',
 'evelyn']

In this instance, we are only looking at three characters. Two input characters, and the character we are predicting next.

e.g. what characters are likely to follow r

we also now what names are likely to start and finish at


We then do a simple count of most prominent trigrams

How many examples do we get from emma?

<S>e -> m
em -> m
mm -> a
ma -> <E>

In [57]:
t = {}
for w in words:
    chs = ['<S>'] + list(w) + ['<E>'] # hallucinate a start character and end character 
    for pair, ch2 in zip(zip(chs, chs[1:]), chs[2:]):
        trigram = (''.join(pair), ch2)
        print(trigram)
        t[trigram] = t.get(trigram, 0) + 1

('<S>e', 'm')
('em', 'm')
('mm', 'a')
('ma', '<E>')
('<S>o', 'l')
('ol', 'i')
('li', 'v')
('iv', 'i')
('vi', 'a')
('ia', '<E>')
('<S>a', 'v')
('av', 'a')
('va', '<E>')
('<S>i', 's')
('is', 'a')
('sa', 'b')
('ab', 'e')
('be', 'l')
('el', 'l')
('ll', 'a')
('la', '<E>')
('<S>s', 'o')
('so', 'p')
('op', 'h')
('ph', 'i')
('hi', 'a')
('ia', '<E>')
('<S>c', 'h')
('ch', 'a')
('ha', 'r')
('ar', 'l')
('rl', 'o')
('lo', 't')
('ot', 't')
('tt', 'e')
('te', '<E>')
('<S>m', 'i')
('mi', 'a')
('ia', '<E>')
('<S>a', 'm')
('am', 'e')
('me', 'l')
('el', 'i')
('li', 'a')
('ia', '<E>')
('<S>h', 'a')
('ha', 'r')
('ar', 'p')
('rp', 'e')
('pe', 'r')
('er', '<E>')
('<S>e', 'v')
('ev', 'e')
('ve', 'l')
('el', 'y')
('ly', 'n')
('yn', '<E>')
('<S>a', 'b')
('ab', 'i')
('bi', 'g')
('ig', 'a')
('ga', 'i')
('ai', 'l')
('il', '<E>')
('<S>e', 'm')
('em', 'i')
('mi', 'l')
('il', 'y')
('ly', '<E>')
('<S>e', 'l')
('el', 'i')
('li', 'z')
('iz', 'a')
('za', 'b')
('ab', 'e')
('be', 't')
('et', 'h')
('th', '<E>')
('<S>m', 'i'

Now lets get the count of each combo and sort. we'll see that ah followed by ending character occurs the

In [108]:
sorted_t = sorted(t.items(), key = lambda kv: -kv[1])

['lw', 'lh', 'tm', 'hj', 'eu', 'nv', 'mc', 'lt', 'ra', 'un', 'hb', 'ek', 'gn', 'iq', 'pm', 'lc', 'ty', 'qs', 'io', 'cq', 'gl', 'mr', 'mb', 'ax', 'sl', 'ti', 'zg', 'cl', 'wk', '<S>t', 'ia', 'mi', 'db', 'ul', 'wg', 'cx', 'lp', 'yk', 'dv', '<S>f', 'so', 'er', 'lb', 'yf', 'oz', '<S>s', 'rl', 'tr', 'wm', 'dz', 'nt', 'hk', 'ju', 'ff', 'hw', 'mw', 'ry', 'iz', 'ng', 'kk', 'oa', 'br', 'rj', 'uo', 'fo', 'ec', 'hz', 'yv', 'wi', 'jb', 'iy', 'vd', 'yr', 'pp', 'yc', 'hs', 'rz', 'ux', 'ze', 'sr', 'de', 'ic', 'hv', 'tf', 'zd', 'rc', 'yl', 'zb', 'ss', 'mt', 'go', 'lm', 'at', 'he', 'ac', 'om', 'nu', 'tn', 'ar', 'dq', 'tl', 'zj', 'ik', 'sp', 'gf', '<S>w', 'mp', 'eh', 'on', 'mm', '<S>v', 'nh', 'az', 'up', 'qm', 'sd', 'op', 'su', 'zm', 'wz', 'pl', 'wf', 'dn', 'os', 'ko', 'sy', 'eg', 'co', 'yg', 'hn', 'gr', 'oc', 'nl', 'as', 'rt', 'eq', 'mf', 'bn', 'qi', 'an', 'be', 'vo', 'zk', 'hl', 'ov', 'ys', 'aw', 'kv', 'ji', 'ug', 'ok', 'rb', 'rm', 'nj', 'bh', 'ig', 'cg', 'fy', 'hq', 'xt', 'fk', 'yb', 'zy', 'mz', 'zi',

Lets convert our trigram to an array. We need to deduce how many rows we have, so it should be all the combinations of characters against our list of 28 chars.

28 characters consist of 26 alphabet characters plus our <S> and <E> characters.

In [90]:
import torch

N = torch.zeros((len(t), 28), dtype=torch.int32)
N
len(t)

6037

We need to create a lookup of integers to pairs so we can have an index. 
Basically we need an integer ref for all our points in our torch, that means each character pair needs an integer value, and each character needs a value e.g. ac = [2000] and if it predicts d as next letter it would be axis point [2000, 3]. Therefore each time this is shown, we add +1, allowing us to count the number of occurences 

If I understand this correctly, we therefore need two integer lookups: 
-
Taking our char pairs as the 'y' axis - we need 0:len(t)  e.g. 0-2000 and then our single character axis being x axis, we need 28 chars (alphabet including <S> and <E>)

0   |------------------------------28
    |<S>aa   <S>ab  <S>ac
    |aaa     aab    aac
    |..
    |..
    |..
6037|zaa zab

Lets get the character string to integer index for our 'y-axis'

In [109]:
# returns all the set of lowercase characters
chars = sorted(set(''.join(words)))
pred_string_to_integer = {s:i for i,s in enumerate(chars)}
pred_string_to_integer['<S>'] = 26
pred_string_to_integer['<E>'] = 27
pred_string_to_integer

{'a': 0,
 'b': 1,
 'c': 2,
 'd': 3,
 'e': 4,
 'f': 5,
 'g': 6,
 'h': 7,
 'i': 8,
 'j': 9,
 'k': 10,
 'l': 11,
 'm': 12,
 'n': 13,
 'o': 14,
 'p': 15,
 'q': 16,
 'r': 17,
 's': 18,
 't': 19,
 'u': 20,
 'v': 21,
 'w': 22,
 'x': 23,
 'y': 24,
 'z': 25,
 '<S>': 26,
 '<E>': 27}

Now lets do our input pairs e.g. lets get the unique values. 

In [111]:
pairs = [item[0][0] for item in sorted_t]
unique_pairs = list(set(pairs))
print(unique_pairs)

['lw', 'lh', 'tm', 'hj', 'eu', 'nv', 'mc', 'lt', 'ra', 'un', 'hb', 'ek', 'gn', 'iq', 'pm', 'lc', 'ty', 'qs', 'io', 'cq', 'gl', 'mr', 'mb', 'ax', 'sl', 'ti', 'zg', 'cl', 'wk', '<S>t', 'ia', 'mi', 'db', 'ul', 'wg', 'cx', 'lp', 'yk', 'dv', '<S>f', 'so', 'er', 'lb', 'yf', 'oz', '<S>s', 'rl', 'tr', 'wm', 'dz', 'nt', 'hk', 'ju', 'ff', 'hw', 'mw', 'ry', 'iz', 'ng', 'kk', 'oa', 'br', 'rj', 'uo', 'fo', 'ec', 'hz', 'yv', 'wi', 'jb', 'iy', 'vd', 'yr', 'pp', 'yc', 'hs', 'rz', 'ux', 'ze', 'sr', 'de', 'ic', 'hv', 'tf', 'zd', 'rc', 'yl', 'zb', 'ss', 'mt', 'go', 'lm', 'at', 'he', 'ac', 'om', 'nu', 'tn', 'ar', 'dq', 'tl', 'zj', 'ik', 'sp', 'gf', '<S>w', 'mp', 'eh', 'on', 'mm', '<S>v', 'nh', 'az', 'up', 'qm', 'sd', 'op', 'su', 'zm', 'wz', 'pl', 'wf', 'dn', 'os', 'ko', 'sy', 'eg', 'co', 'yg', 'hn', 'gr', 'oc', 'nl', 'as', 'rt', 'eq', 'mf', 'bn', 'qi', 'an', 'be', 'vo', 'zk', 'hl', 'ov', 'ys', 'aw', 'kv', 'ji', 'ug', 'ok', 'rb', 'rm', 'nj', 'bh', 'ig', 'cg', 'fy', 'hq', 'xt', 'fk', 'yb', 'zy', 'mz', 'zi',

In [87]:
for w in words:
    chs = ['<S>'] + list(w) + ['<E>'] # hallucinate a start character and end character 
    for ch1, ch2 in zip(chs, chs[1:]):
        ix1 = string_to_integer[ch1]
        ix2 = string_to_integer[ch2]
        N[ix1, ix2] += 1

N[0]

tensor([ 1112,  1082,   940,  2084,  1384,   268,   336,  4664,  3300,   350,
         1136,  5056,  3268, 10876,   126,   164,   120,  6528,  2236,  1374,
          762,  1668,   322,   364,  4100,   870,     0, 13280],
       dtype=torch.int32)